In [1]:
!pip install transformers
!pip install evaluate
!pip install rouge


import torch
import json
from tqdm import tqdm
import torch.nn as nn
from torch.optim import Adam
import nltk
import spacy
import string
import evaluate  # Bleu
from torch.utils.data import Dataset, DataLoader, RandomSampler
import pandas as pd
import numpy as np
import transformers
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt
from transformers import T5Tokenizer, T5Model, T5ForConditionalGeneration, T5TokenizerFast

import warnings
warnings.filterwarnings("ignore")

  Obtaining dependency information for evaluate from https://files.pythonhosted.org/packages/70/63/7644a1eb7b0297e585a6adec98ed9e575309bb973c33b394dae66bc35c69/evaluate-0.4.1-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 4.7 MB/s eta 0:00:00
  Obtaining dependency information for rouge from https://files.pythonhosted.org/packages/32/7c/650ae86f92460e9e8ef969cc5008b24798dcf56a9a8947d04c78f550b3f5/rouge-1.0.1-py3-none-any.whl.metadata


/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
TOKENIZER = T5TokenizerFast.from_pretrained("t5-base")
MODEL = T5ForConditionalGeneration.from_pretrained("t5-base", return_dict=True)
OPTIMIZER = Adam(MODEL.parameters(), lr=0.00001)
Q_LEN = 256
T_LEN = 32
BATCH_SIZE = 10
DEVICE = "cuda:0"

In [3]:
import json
import pandas as pd

In [4]:
# Loading the data
with open('../input/stanford-question-answering-dataset/train-v1.1.json') as f:
    data = json.load(f)

In [5]:
def prepare_data(data):
    articles = []
    
    for article in data["data"]:
        for paragraph in article["paragraphs"]:
            for qa in paragraph["qas"]:
                question = qa["question"]
                answer = qa["answers"][0]["text"]
                inputs = {"context": paragraph["context"], "question": question, "answer": answer}
                articles.append(inputs)

    return articles

In [6]:
data = prepare_data(data)
data = pd.DataFrame(data)
data = data.loc[:3000]

In [7]:
data.shape

(3001, 3)

In [8]:
class QA_Dataset(Dataset):
    def __init__(self, tokenizer, dataframe, q_len, t_len):
        self.tokenizer = tokenizer
        self.q_len = q_len
        self.t_len = t_len
        self.data = dataframe
        self.questions = self.data["question"]
        self.context = self.data["context"]
        self.answer = self.data['answer']
        
    def __len__(self):
        return len(self.questions)
    
    def __getitem__(self, idx):
        question = self.questions[idx]
        context = self.context[idx]
        answer = self.answer[idx]
        
        question_tokenized = self.tokenizer(question, context, max_length=self.q_len, padding="max_length",
                                                    truncation=True, pad_to_max_length=True, add_special_tokens=True)
        answer_tokenized = self.tokenizer(answer, max_length=self.t_len, padding="max_length", 
                                          truncation=True, pad_to_max_length=True, add_special_tokens=True)
        
        labels = torch.tensor(answer_tokenized["input_ids"], dtype=torch.long)
        labels[labels == 0] = -100
        
        return {
            "input_ids": torch.tensor(question_tokenized["input_ids"], dtype=torch.long),
            "attention_mask": torch.tensor(question_tokenized["attention_mask"], dtype=torch.long),
            "labels": labels,
            "decoder_attention_mask": torch.tensor(answer_tokenized["attention_mask"], dtype=torch.long)
        }

In [9]:
# Dataloader

train_data, val_data = train_test_split(data, test_size=0.2, random_state=42)

train_sampler = RandomSampler(train_data.index)
val_sampler = RandomSampler(val_data.index)

qa_dataset = QA_Dataset(TOKENIZER, data, Q_LEN, T_LEN)

train_loader = DataLoader(qa_dataset, batch_size=BATCH_SIZE, sampler=train_sampler)
val_loader = DataLoader(qa_dataset, batch_size=BATCH_SIZE, sampler=val_sampler)

In [10]:
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
MODEL.to(DEVICE)
OPTIMIZER = torch.optim.Adam(MODEL.parameters(), lr=0.00001)

In [11]:
train_loss = 0
val_loss = 0
train_batch_count = 0
val_batch_count = 0
em_count = 0
total_questions = 0

for epoch in range(5):
    MODEL.train()
    for batch in tqdm(train_loader, desc = "Training batches"):
        input_ids = batch["input_ids"].to(DEVICE)
        attention_mask = batch["attention_mask"].to(DEVICE)
        labels = batch["labels"].to(DEVICE)
        decoder_attention_mask = batch["decoder_attention_mask"].to(DEVICE)

        outputs = MODEL(
            input_ids = input_ids,
            attention_mask = attention_mask,
            labels = labels,
            decoder_attention_mask = decoder_attention_mask
        )

        OPTIMIZER.zero_grad()
        outputs.loss.backward()
        OPTIMIZER.step()
        train_loss += outputs.loss.item()
        train_batch_count += 1
    
    # Evaluation
    MODEL.eval()
    for batch in tqdm(val_loader, desc = "Validation batches"):
        input_ids = batch["input_ids"].to(DEVICE)
        attention_mask = batch["attention_mask"].to(DEVICE)
        labels = batch["labels"].to(DEVICE)
        decoder_attention_mask = batch["decoder_attention_mask"].to(DEVICE)

        outputs = MODEL(
            input_ids = input_ids,
            attention_mask = attention_mask,
            labels = labels,
            decoder_attention_mask = decoder_attention_mask
        )

        val_loss += outputs.loss.item()
        val_batch_count += 1
        
        predictions = MODEL.generate(input_ids = input_ids, attention_mask = attention_mask)
        for i in range(len(predictions)):
            predicted_answer = TOKENIZER.decode(predictions[i], skip_special_tokens = True)
            print(labels)
            label_mask = labels[i] != -100
            true_answer = TOKENIZER.decode(labels[i][label_mask], skip_special_tokens=True)
#             true_answer = TOKENIZER.decode(labels[i], skip_special_tokens=True)
            if predicted_answer.lower() == true_answer.lower():
                em_count += 1
            total_questions += 1


    print(f"{epoch+1}/{5} -> Train loss: {train_loss / train_batch_count}\tValidation loss: {val_loss/val_batch_count}")

Validation batches:   2%|▏         | 1/61 [00:01<01:49,  1.83s/it]

tensor([[  991,  7634,     1,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [ 2391,     1,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [11031,  3035,  1850,     1,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [ 1762,  7973,  1673,     1,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  

Validation batches:   3%|▎         | 2/61 [00:02<00:59,  1.00s/it]

tensor([[24884,     1,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [   30,  2239,    12,  6224,     1,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [  966,   314,   770,     1,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [   37,  8667,     5, 17080,  3111,  1150,  3351,     1,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  

Validation batches:   5%|▍         | 3/61 [00:02<00:42,  1.35it/s]

...

tensor([[ 1193, 18301,   257,    13,  6679,  4737,     1,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [ 9373,  1027,     1,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [  505, 11212,  2812,  1922,     1,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [10662,  2419,    11,  2540, 20710,     1,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  

Validation batches:  98%|█████████▊| 60/61 [00:24<00:00,  2.37it/s]

tensor([[13331,  4895,     1,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [  874,     1,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [21625,    11,  6751,    51,     9,     1,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100],
        [ 6946,  2549, 10846,     7,     1,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,  -100,
          -100,  -100,  -100,  -100,  -100,  -100,  -100,  

Validation batches: 100%|██████████| 61/61 [00:24<00:00,  2.46it/s]

tensor([[  37,  493,   63,  106,   75,  154, 7187,    1, -100, -100, -100, -100,
         -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100, -100,
         -100, -100, -100, -100, -100, -100, -100, -100]], device='cuda:0')
5/5 -> Train loss: 1.0866124098841101	Validation loss: 0.6688844150970461


In [12]:
avg_train_loss = train_loss / train_batch_count
avg_val_loss = val_loss / val_batch_count
em_accuracy = em_count / total_questions

print(f"Average Training loss: {avg_train_loss}")
print(f"Average Testing loss: {avg_val_loss}")
print(f"Exact match Score: {em_accuracy}")

Average Training loss: 1.0866124098841101
Average Testing loss: 0.6688844150970461
Exact match Score: 0.5537437603993345


In [13]:
MODEL.save_pretrained("qa_model")
TOKENIZER.save_pretrained("qa_tokenizer")

# Saved files
"""('qa_tokenizer/tokenizer_config.json',
 'qa_tokenizer/special_tokens_map.json',
 'qa_tokenizer/spiece.model',
'qa_tokenizer/added_tokens.json',
'qa_tokenizer/tokenizer.json')"""

"('qa_tokenizer/tokenizer_config.json',\n 'qa_tokenizer/special_tokens_map.json',\n 'qa_tokenizer/spiece.model',\n'qa_tokenizer/added_tokens.json',\n'qa_tokenizer/tokenizer.json')"

In [14]:
def predict_answer(context, question, ref_answer = None):
    inputs = TOKENIZER(question, context, max_length = Q_LEN, padding="max_length", truncation = True, add_special_tokens = True)
    
    input_ids = torch.tensor(inputs["input_ids"], dtype = torch.long).to(DEVICE).unsqueeze(0)
    attention_mask = torch.tensor(inputs["attention_mask"], dtype = torch.long).to(DEVICE).unsqueeze(0)

    outputs = MODEL.generate(input_ids = input_ids, attention_mask = attention_mask)
  
    predicted_answer = TOKENIZER.decode(outputs.flatten(), skip_special_tokens = True)
    
    if ref_answer:
        bleu = evaluate.load("google_bleu")
        print(predicted_answer, ref_answer)
        score = bleu.compute(predictions = [predicted_answer], references = [ref_answer])
    
        print("Context: \n", context)
        print("\n")
        print("Question: \n", question)
        return {
            "Reference Answer: ": ref_answer, 
            "Predicted Answer: ": predicted_answer, 
            "BLEU Score: ": score
        }
    else:
        return predicted_answer

In [15]:
context = data.iloc[0]["context"]
question = data.iloc[0]["question"]
answer = data.iloc[0]["answer"]

In [16]:
predict_answer(context, question, answer)

Saint Bernadette Soubirous Saint Bernadette Soubirous
Context: 
 Architecturally, the school has a Catholic character. Atop the Main Building's gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend "Venite Ad Me Omnes". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.


Question: 
 To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?


{'Reference Answer: ': 'Saint Bernadette Soubirous',
 'Predicted Answer: ': 'Saint Bernadette Soubirous',
 'BLEU Score: ': {'google_bleu': 1.0}}

In [17]:
context = """Virat Kohli on Tuesday slammed his 73rd international hundred by reaching the three-figure mark off 80 deliveries against Sri Lanka in first ODI in Guwahati. 
The 34-year-old became the fastest batter to slam 20 ODI hundreds on Indian soil, taking 99 innings. 
He also overtook Sachin Tendulkar to become the fastest batter to smash 45 ODI hundreds, taking 257 innings."""

In [18]:
q_1 = "How many innings does Virat Kohli took to reach 45 ODI hundreds?" 
predict_answer(context, q_1)

'257'

In [19]:
q_2 = "Whom did Virat Kohli overtook to become faster batsmen to smash 45 ODI hundreds?" 
predict_answer(context, q_2)

'Sachin Tendulkar'

In [20]:
q_3 = "Which team did Virat Kohli score his 45th ODI century against?" 
predict_answer(context, q_3)

'Sri Lanka'

In [21]:
q_4="How many international hundreds did Virat Kohli score?" 
predict_answer(context, q_4)

'73'